## Array Sections in Device Constructs

The following examples show the usage of array sections in __map__ clauses  on __target__ and __target__ __data__ constructs.

This example shows the invalid usage of two separate sections of the same array  inside of a __target__ construct.

In [ ]:
//%compiler: clang
//%cflags: -fopenmp

/*
* name: array_sections.1
* type: C
* version: omp_4.0
*/
void foo ()
{
   int A[30];
#pragma omp target data map( A[0:4] )
{
   /* Cannot map distinct parts of the same array */
   #pragma omp target map( A[7:20] )
   {
      A[2] = 0;
   }
}
}

In [ ]:
!!%compiler: gfortran
!!%cflags: -fopenmp

! name: array_sections.1
! type: F-free
! version: omp_4.0
subroutine foo()
integer :: A(30)
   A = 1
   !$omp target data map( A(1:4) )
     ! Cannot map distinct parts of the same array
     !$omp target map( A(8:27) )
        A(3) = 0
     !$omp end target
   !$omp end target data
end subroutine

This example shows the invalid usage of two separate sections of the same array  inside of a __target__ construct.

In [ ]:
//%compiler: clang
//%cflags: -fopenmp

/*
* name: array_sections.2
* type: C
* version: omp_4.0
*/
void foo ()
{
   int A[30], *p;
#pragma omp target data map( A[0:4] )
{
   p = &A[0];
   /* invalid because p[3] and A[3] are the same
    * location on the host but the array section
    * specified via p[...] is not a subset of A[0:4] */
   #pragma omp target map( p[3:20] )
   {
      A[2] = 0;
      p[8] = 0;
   }
}
}

In [ ]:
!!%compiler: gfortran
!!%cflags: -fopenmp

! name: array_sections.2
! type: F-free
! version: omp_4.0
subroutine foo()
integer,target  :: A(30)
integer,pointer :: p(:)
   A=1
   !$omp target data map( A(1:4) )
     p=>A
     ! invalid because p(4) and A(4) are the same
     ! location on the host but the array section
     ! specified via p(...) is not a subset of A(1:4)
     !$omp target map( p(4:23) )
        A(3) = 0
        p(9) = 0
     !$omp end target
   !$omp end target data
end subroutine

This example shows the valid usage of two separate sections of the same array inside  of a __target__ construct.

In [ ]:
//%compiler: clang
//%cflags: -fopenmp

/*
* name: array_sections.3
* type: C
* version: omp_4.0
*/
void foo ()
{
   int A[30], *p;
#pragma omp target data map( A[0:4] )
{
   p = &A[0];
   #pragma omp target map( p[7:20] )
   {
      A[2] = 0;
      p[8] = 0;
   }
}
}

In [ ]:
!!%compiler: gfortran
!!%cflags: -fopenmp

! name: array_sections.3
! type: F-free
! version: omp_4.0
subroutine foo()
integer,target  :: A(30)
integer,pointer :: p(:)
   !$omp target data map( A(1:4) )
     p=>A
     !$omp target map( p(8:27) )
        A(3) = 0
        p(9) = 0
     !$omp end target
   !$omp end target data
end subroutine

This example shows the valid usage of a wholly contained array section of an already  mapped array section inside of a __target__ construct.

In [ ]:
//%compiler: clang
//%cflags: -fopenmp

/*
* name: array_sections.4
* type: C
* version: omp_4.0
*/
void foo ()
{
   int A[30], *p;
#pragma omp target data map( A[0:10] )
{
   p = &A[0];
   #pragma omp target map( p[3:7] )
   {
      A[2] = 0;
      p[8] = 0;
      A[8] = 1;
   }
}
}

In [ ]:
!!%compiler: gfortran
!!%cflags: -fopenmp

! name: array_sections.4
! type: F-free
! version: omp_4.0
subroutine foo()
integer,target  :: A(30)
integer,pointer :: p(:)
   !$omp target data map( A(1:10) )
     p=>A
     !$omp target map( p(4:10) )
        A(3) = 0
        p(9) = 0
        A(9) = 1
     !$omp end target
   !$omp end target data
end subroutine